$\newcommand\N{\mathbb N}
\newcommand\Z{\mathbb Z}
\newcommand\Q{\mathbb Q}
\newcommand\R{\mathbb R}
\newcommand\C{\mathbb C}
\newcommand\too\longrightarrow
\renewcommand\phi\varphi
\renewcommand\epsilon\varepsilon
\newcommand\fl[1]{\left\lfloor #1\right\rfloor}
\newcommand\llbracket{[\![}
\newcommand\rrbracket{]\!]}
\newcommand\bbr[2]{\llbracket #1,#2\rrbracket}
\newcommand\todo{{\bf TODO }}
\newcommand\prob{\mathbb P}
\newcommand\esp{\mathbb E}
\newcommand\var{\mathbb V}
\newcommand\tribu{\mathfrak T}$

# L'électricien sournois

Marc Lorenzi

27 août 2024

In [ ]:
import matplotlib.pyplot as plt
import random
import time

## 1. Introduction

### 1.1 Description du jeu

Une installation électrique comporte $n$ lampes et $n$ boutons. Chaque bouton *est censé* changer l'état de la lampe correspondante (allumée ou éteinte). Le problème est que l'installation a été faite par un électricien sournois. Quand on appuie sur un bouton, il change l'état de la lampe correspondante, *mais aussi l'état de certaines autres lampes*. Au départ, toutes les lampes sont éteintes. Le but du jeu est de les allumer toutes.

Nous prendrons dans la suite l'exemple suivant (où $n=8$). On numérote les lampes et les boutons de 0 à 7.

- L'appui sur le bouton 0 bascule l'état des lampes 0, 1, 2, 6, 7
- L'appui sur le bouton 1 bascule l'état des lampes 1, 3, 7
- L'appui sur le bouton 2 bascule l'état des lampes 1, 2, 3
- L'appui sur le bouton 3 bascule l'état des lampes 1, 3, 5
- L'appui sur le bouton 4 bascule l'état des lampes 2, 3, 4, 5, 6
- L'appui sur le bouton 5 bascule l'état des lampes 3, 5, 7
- L'appui sur le bouton 6 bascule l'état des lampes 5, 6, 7
- L'appui sur le bouton 7 bascule l'état des lampes 1, 5, 7

Nous allons voir que derrière ce jeu apparemment sans aucun intérêt se cachent des espaces vectoriels sur le corps à deux éléments et l'algorithme du pivot de Gauss.

### 1.2 L'approche « c'est évident »

Dans la règle du jeu, nous voyons que chaque entier entre 0 et 7 apparaît un nombre impair de fois. Or, si une lampe est éteinte et que nous appuyons sur l'interrupteur un nombre impair de fois, la lampe est allumée. Donc, si nous appuyons sur tous les boutons l'un après l'autre, toutes les lampes seront allumées.

Le problème est que cet argument ne fonctionne que sur l'exemple choisi. Pour une autre installation électrique, cet argument ne fonctionnera plus. Nous allons voir dans ce notebook qu'il est possible de trouver une solution au jeu de façon générale, avec $n$ lampes et $n$ boutons qui changent l'état de certaines des $n$ lampes. Notre algorithme effectuera $O(n^2)$ opérations sur des entiers.

### 1.3 L'approche enfantine

On représente un état du jeu par un entier $x\in\bbr 0{255}$. Précisément, écrivons

$$x=\sum_{k=0}^7 b_{k}2^{k}$$

Si $b_k=0$ (resp : $b_k=1$) alors la lampe $k$ est éteinte (resp : allumée). Par exemple, prenons $x=114$. On a, en base 2,

$$x=01110010$$

Rappelons que les bits se lisent de droite à gauche ! Les bits 1, 4, 5 et 6 de $x$ sont à 1, donc les lampes 1, 4, 5 et 6 sont allumées et les autres lampes sont éteintes.

L'état initial du jeu est 0 et l'état final est 255.

La variable `exemple` est une liste dont le $k$ème élément est un entier de 8 bits qui décrit les lampes dont l'état change quand on appuie sur le bouton $k$. Pour $j\in\bbr 07$, si le bit $j$ est à 1, la lampe $j$ change d'état. Sinon, elle ne change pas d'état.

In [ ]:
exemple = [0b11000111, 0b10001010, 0b00001110, 0b00101010, 0b01111100, 0b10101000, 0b11100000, 0b10100010]
print(exemple)

L'appui sur un bouton est réalisé par la fonction `appuyer`. Pour appuyer sur l'interrupteur $k$, on réalise un ou exclusif entre les bits de l'état $x$ et ceux de l'entier `exemple[k]`. L'opérateur Python `^` effectue cette opération.

In [ ]:
def appuyer(x, k): return x ^ exemple[k]

L'approche enfantine consiste à appuyer sur des boutons au hasard. On finira bien par allumer les lampes ... La fonction `jeu_enfantin` renvoie le nombre d'appuis sur des boutons nécessaires pour aller de l'état `debut` à l'état `fin`.

In [ ]:
def jeu_enfantin(debut, fin):
    x = debut
    c = 0
    while x != fin:
        k = random.randint(0, 7)
        x = appuyer(x, k)
        c += 1
    return c

In [ ]:
jeu_enfantin(0, 255)

Cette approche est **très** naïve, vu que si on appuie deux fois sur le même bouton, les actions s'annulent. Il suffit donc d'appuyer uniquement sur des boutons différents. C'est l'objet du paragraphe suivant.

### 1.4 L'approche naïve

La fonction `jeu_naif` fonctionne comme suit. Pour chaque partie $A$ de $\bbr 07$ elle appuie sur les boutons dont le numéro appartient à $A$. S'il existe une solution, elle ne peut que réussir ... mais au bout d'un certain temps.

La fonction `parties` énumère les parties d'un ensemble $E$ donné par la liste de ses éléments.

In [ ]:
def parties(E):
    if len(E) == 0: yield []
    else:
        a = E[0]
        E1 = E[1:]
        for A in parties(E1):
            yield A
            yield [a] + A

In [ ]:
for A in parties([0, 1, 2, 3]):
    print(A, end=' ')

La fonction `jeu_naif` opère comme la fonction `jeu_tres_naif`. Elle renvoie la solution trouvée et le nombre de parties de $\bbr 0 7$ que l'on a testées.

In [ ]:
def jeu_naif(debut, fin):
    c = 0
    for A in parties(list(range(8))):
        x = debut
        c += 1
        for k in A:
            x = appuyer(x, k)
        if x == fin: return A, c

In [ ]:
jeu_naif(0, 255)

Dans le pire des cas, l'approche naïve sur un jeu de taille $n$ teste toutes les parties de l'ensemble $\bbr 0{n-1}$. Il y en a $2^n$, ce qui nous donne une complexité exponentielle. C'est clairement inacceptable : il va nous falloir trouver mieux.

### 1.5 Quelques remarques

Comme nous l'avons vu, si nous appuyons successivement sur les boutons 0, 1, ..., 7 nous allumons toutes les lampes.

In [ ]:
x = 0
for k in range(8):
    x = appuyer(x, k)
    print(x, end=' ')

Gagné. Et si on appuie sur les boutons de 0 à 7 dans un ordre aléatoire ?

In [ ]:
x = 0
s = list(range(8))
random.shuffle(s)
print(s)
for k in s:
    x = appuyer(x, k)
    print(x, end=' ')

Cela ne change rien. Bien que les états intermédiaires soient différents, on gagne à chaque fois. Et qu'arrive-t-il si on modifie l'effet de l'appui sur un bouton ? Si on change l'état de départ ? L'état d'arrivée ? Et quel est le nombre minimal d'appuis nécessaires pour gagner pour un jeu donné ? Etc.

**Bref, mathématisons le jeu pour mieux le comprendre et pour obtenir une solution générale.**

## 2. Algèbre linéaire

### 2.1 Un espace vectoriel

Soit $\mathbb K=\{0,1\}$ le corps à deux éléments. Soit $E=\mathbb K^n$, qui est un $\mathbb K$-espace vectoriel de dimension $n$.

Modélisons un état du jeu par un vecteur $x=(x_0,\ldots,x_{n-1})\in E$. Si $x_k=0$, la lampe $k$ est éteinte. Sinon, elle est allumée.

Les appuis sur des boutons peuvent eux aussi être représentés par des vecteurs de $E$. Pour $k\in\bbr 0{n-1}$, soit $e_k$ le vecteur « appui sur le bouton $k$ ». Si $x\in E$ est un état du jeu, alors $x+e_k$ est l'état du jeu après avoir appuyé sur le bouton $k$ en partant de l'état $x$. 

La famille $\mathcal B=(e_0,\ldots,e_{n-1})$ est de cardinal $n=\dim E$. En supposant que $\mathcal B$ est une base de $E$, tout vecteur $x$ de $E$ s'écrit alors de façon unique

$$x=\sum_{k=0}^{n-1} x_ke_k$$

où les $x_k$ appartiennent à $\mathbb K$. Trouver « une » solution du jeu revient à trouver les coordonnées $x_k$ du vecteur $(1,\ldots,1)$ dans la base $\mathcal B$. Pour terminer le jeu il suffit d'appuyer sur les boutons $k$ tels que $x_k=1$. Et l'ordre dans lequel on appuie n'a aucune importance puisque l'addition des vecteurs est commutative. Mieux, il y a unicité de la solution modulo 2. Si $x_k=0$ (resp : 1) il faut appuyer un nombre pair (resp : impair) de fois sur le bouton $k$.

Nous voici donc ramenés à un problème classique d'algèbre linéaire : trouver les coordonnées $x_0,\ldots,x_{n-1}$ du vecteur $y=(1,\ldots, 1)$ dans la base $\mathcal B$.

Notons $\mathcal B_0$ la base canonique de $E$. Soit $P$ la matrice de passage de $\mathcal B_0$ à $\mathcal B$. On a par les formules de changement de bases

$$(1 \ldots 1)^T=P(x_0\ldots x_{n-1})^T$$

Notre problème se ramène donc à la résolution du système $PX=Y$.

### 2.2 Modélisation

 En identifiant les éléments de $\mathbb K$ avec les entiers 0 et 1, la fonction $\phi: E\too\bbr 0{2^n-1}$ définie par

$$\phi(x_0,\ldots,x_{n-1})=\sum_{k=0}^{n-1} x_k2^k$$

est une bijection. Les opérations dans $E$ sont faciles à décrire via la bijection $\phi$. Le produit par un scalaire est trivial, vu qu'il n'y a que deux scalaires, 0 et 1. L'addition des vecteurs est également très simple. Si $x,y\in E$, on a

$$\phi(x+y)=\sum_{k=0}^{n-1} (x_k\oplus y_k)2^k$$

où $x_k\oplus y_k$ est une addition dans le corps $\mathbb K$. Cette somme vaut 1 si $x_k\ne y_k$ et 0 sinon. En d'autres termes, $x_k\oplus y_k$ est le « ou exclusif » de $x_k$ et $y_k$. Si nous identifions $E$ avec $\bbr 0{2^n-1}$, additionner deux vecteurs revient donc à faire un ou exclusif entre les bits des entiers correspondants. C'est précisément ce que fait l'opérateur Python `^`.


### 2.3 Transposition

Soit $A=(A_0,\ldots,A_{n-1})$ une liste de $n$ entiers. Supposons que ces entiers peuvent s'écrire sur $n$ bits. Ces entiers peuvent être vus comme des vecteurs de l'espace vectoriel $E=\mathbb K^n$ : pour tout $i\in\bbr 0{n-1}$,

$$A_i=\sum_{j=0}^{n-1}A_{ij}2^j$$

où les $A_{ij}$ appartiennent à $\mathbb K$. La liste $A$ peut donc aussi être vue comme la matrice $(A_{ij})_{0\le i,j\le n-1}\in \mathcal M_n(\mathbb K)$.

Prenons par exemple la liste $\mathcal L$ des vecteurs « appui sur un bouton ». Cette liste, vue comme une matrice, est la matrice des vecteurs de $\mathcal B$ *écrits en ligne*. La matrice de passage de la base $\mathcal B_0$ à la base $\mathcal B$ est, quant à elle, la matrice des vecteurs de $\mathcal B$ *écrits en colonne*. Il convient donc d'écrire une fonction qui transpose une matrice.

En reprenant les notations ci-dessus, soit $B=A^T$. En interprétant $B$ comme une liste $(B_0,\ldots,B_{n-1})$ de $n$ entiers, on a pour tout $i\in\bbr 0{n-1}$,

$$B_i=\sum_{j=0}^{n-1}B_{ij}2^j=\sum_{j=0}^{n-1}A_{ji}2^j$$

La fonction `bit` prend en paramètres deux entiers $x$ et $i$. Elle renvoie le $i$ème bit de $x$. Il suffit pour cela de décaler $x$ de $i$ bits vers la droite et de renvoyer le bit de poids faible.

In [ ]:
def bit(x, i): return (x >> i) & 1

La fonction `transp` prend en paramètre une liste $A$ d'entiers interprétée comme une matrice. Elle renvoie $A^T$, sous forme d'une liste de $n$ entiers. Remarquons que la complexité de `transp` est, en nombre d'opérations sur des entiers, $O(n^2)$.

In [ ]:
def transp(A):
    n = len(A)
    B = []
    for i in range(n):
        x = 0
        for j in range(n):
            x = (x << 1) | bit(A[n - 1 - j], i)
        B.append(x)
    return B

Voici la matrice de passage de $\mathcal B_0$ à $\mathcal B$.

In [ ]:
P = transp(exemple)
print(P)

À titre de vérification, une nouvelle transposée devrait redonner la liste `regle`.

In [ ]:
print(transp(P) == exemple)

## 3. Le pivot de Gauss

Pour trouver la solution du jeu, il suffit de résoudre un système linéaire. La façon la plus élégante de le faire est d'utiliser le pivot de Gauss. *Je vais supposer que le lecteur sait comment fonctionne cet algorithme.*

Commençons par écrire quelques fonctions utiles.

### 3.1 Fonctions utiles

La fonction `eye` renvoie la matrice identité d'ordre $n$. Interprétée comme une liste d'entiers, cette matrice est

$$(2^0,2^1,\ldots, 2^{n-1})$$

In [ ]:
def eye(n):
    return [2 ** k for k in range(n)]

In [ ]:
print(eye(8))

Pour tester les fonctions que nous allons écrire, il sera bon de pouvoir fabriquer des exemples « à la volée ». La fonction `rand_mat` renvoie une liste de $n$ entiers aléatoires ayant au plus $n$ bits.

In [ ]:
def rand_mat(n):
    return [random.randint(0, 2 ** n - 1) for k in range(n)]

In [ ]:
A = rand_mat(8)
print(A)

### 3.2 Opérations sur les lignes

La fonction `ech` échange les lignes $i_1$ et $i_2$ de la matrice $A$. Sa complexité est $O(1)$.

In [ ]:
def ech(A, i1, i2): A[i1], A[i2] = A[i2], A[i1]

La fonction `add` ajoute à la ligne $i_1$ de la matrice $A$ sa ligne $i_2$. Rappelons nous que nos matrices sont à coefficients dans le corps $\mathbb K$. L'addition s'effectue donc en faisant un ou exclusif. Sa complexité est aussi $O(1)$ (à condition que la taille de $A$ soit inférieure à la taille des entiers « machine », qui est sans doute 64).

In [ ]:
def add(A, i1, i2): A[i1] = A[i1] ^ A[i2]

### 3.3 Pivoter

La fonction `rech_pivot` prend en paramètres une matrice $A$ et un entier $k$. Elle cherche dans la colonne $k$ de $A$, parmi $A_{kk}$, $A_{(k+1)k}$, etc. un coefficient égal à 1. Elle renvoie l'indice de ligne de ce coefficient. Si elle ne trouve pas un tel coefficient, elle renvoie la taille de $A$. La complexité de cette fonction est $O(n-k)=O(n)$ où $n$ est la taille de $A$.

In [ ]:
def rech_pivot(A, k):
    n = len(A)
    for i in range(k, n):
        if bit(A[i], k) == 1:
            return i
    return n

La fonction `pivoter` prend en paramètres deux matrices $A$ et $B$, ainsi qu'un entier $k$.

- Elle commence par rechercher un entier $i\ge k$ tel que $A_{ik}=1$. Si elle n'en trouve pas, la théorie de l'algorithme du pivot de Gauss nous dit que $A$ n'est pas inversible. La fonction lève alors une exception.
- La fonction échange les lignes $i$ et $k$ des matrices $A$ et $B$.
- Pour tout $i\ne k$, si $A_{ik}=1$, la fonction ajoute à la ligne $i$ de $A$ la ligne $k$ de $A$, et de même pour $B$. Ceci a pour effet d'annuler $A_{ik}$. En effet, $A_{ik}=A_{kk}=1$ et donc $A_{ik}\land A_{kk}=0$ (le $\land$ est un ou exclusif).

Remarquons que comme nos fonctions `ech` et `add` ont une complexité en $O(1)$, la complexité de `pivoter` est $O(n)$. Dans un pivot de Gauss « classique », cette complexité serait $O(n^2)$.

In [ ]:
def pivoter(A, B, k):
    n = len(A)
    i = rech_pivot(A, k)
    if i == n:
        raise Exception('Non inversible')
    else:
        ech(A, i, k)
        ech(B, i, k)
        for i in range(n):
            if i != k and bit(A[i], k) == 1:
                add(A, i, k)
                add(B, i, k)

### 3.4 Résoudre

La fonction `gauss` prend en paramètres deux matrices $A$ et $B$ (c'est à dire, avec nos conventions, deux listes d'entiers) de même taille. Elle résout le système $AX=B$ d'inconnue $X$. Si la matrice $A$ n'est pas inversible, une exception est levée par l'appel à `pivoter`. La complexité de `gauss` est $O(n^2)$ (à comparer avec le $O(n^3)$ du pivot classique).

In [ ]:
def gauss(A, B):
    A, B = A[:], B[:]
    n = len(A)
    for k in range(n):
        pivoter(A, B, k)
    return A, B

Cela ne coûte rien, le pivot de Gauss permet le calcul de l'inverse d'une matrice. Ici, en $O(n^2)$.

In [ ]:
def inverse(A):
    n = len(A)
    A1, B1 = gauss(A, eye(n))
    return B1

Testons. Comme nous prenons une matrice aléatoire, il est possible qu'une exception soit levée. Il n'y a qu'à réévaluer la cellule.

In [ ]:
try:
    A = rand_mat(8)
    B = inverse(A)
    print(A)
    print(B)
except Exception:
    print('C\'est raté')

On tombe assez souvent sur des matrices non inversibles. Comment cela se fait-il ? Le cardinal de $\mathcal M_n(\mathbb K)$ est

$$|\mathcal M_n(\mathbb K)|=|\mathbb K|^{n^2}=2^{n^2}$$

Pour fabriquer une matrice inversible, on crée ses colonnes $C_0,C_1,\ldots,C_{n-1}$ en faisant en sorte que pour tout $k\in\bbr0{n-1}$, la colonne $C_k$ ne soit pas combinaison linéaire des colonnes $C_0,\ldots,C_{k-1}$. Remarquons que le nombre de telles combinaisons linéaires est $2^k$.

- On choisit $C_0$ non nulle : $2^n-1$ possibilités.
- On choisit $C_1$ non colinéaire à la colonne 0 : $2^n-2^1$ possibilités.
- On choisit $C_2$ non combinaison linéaire de $C_0$ et $C_1$ : $2^n-2^2$ possibilités.
- ...
- On choisit $C_k$ non combinaison linéaire de $C_0,\ldots,C_{k-1}$ : $2^n-2^k$ possibilités.
- ...
- On choisit $C_{n-1}$ non combinaison linéaire de $C_0,\ldots,C_{n-1}$ : $2^n-2^{n-1}$ possibilités.

Le cardinal de $GL_n(\mathbb K)$ est donc

$$|GL_n(\mathbb K)|=\prod_{k=0}^{n-1}(2^n-2^k)=\prod_{k=1}^{n}(2^n-2^{n-k})=\prod_{k=1}^{n}2^n(1-2^{-k})$$

Munissons $\mathcal M_n(\mathbb K)$ de la probabilité uniforme $\prob$. La probabilité de $GL_n(\mathbb K)$ est alors

$$\prob(GL_n(\mathbb K))=\frac{|GL_n(\mathbb K)|}{|\mathcal M_n(\mathbb K)|}=\prod_{k=1}^{n}\left(1-\frac 1{2^{k}}\right)$$

In [ ]:
def proba_inversible(p, n):
    x = 1
    for k in range(1, n + 1):
        x *= 1 - 1 / (p ** k)
    return x

In [ ]:
print(proba_inversible(2, 8))

Il y a moins de 30% de chances qu'une matrice de taille 8 soit inversible, d'où le commentaire que j'ai fait un peu plus haut sur la réévaluation fort possible d'une certaine cellule.

**Remarque.** Le produit infini

$$\prod_{k=1}^{\infty}\left(1-\frac 1{2^{k}}\right)$$

est convergent. De même, pour tout réel $x>1$, le produit infini

$$\psi(x)=\prod_{k=1}^{\infty}\left(1-\frac 1{x^{k}}\right)$$

Il y a énormément de choses à dire sur la fonction $\psi$ mais cela nous éloignerait de notre sujet ... Le lecteur intéressé pourra se documenter sur la notion de *$q$-symbole de Pochhammer*.


L'errrur commise en approchant $\psi(2)$ par le produit pour $k$ allant de 1 à $n$ est de l'ordre de $1/2^n$. La convergence est donc relativement rapide. Remarquons que pour Python,

In [ ]:
1 - 1 / (2 ** 53)

In [ ]:
1 - 1 / (2 ** 54)

Inutile, donc, de prendre $n\ge 54$. Nous ne ferions que des multiplications par 1 dans la fonction `proba_inversible`. Une bonne valeur de $\psi(2)$ est donc sans doute

In [ ]:
print(proba_inversible(2, 53))

### 3.5 Vérifications

La fonction `mul` effectue le produit des matrices $A$ et $B$, supposées carrées. Rappelons nous que le corps de base est $\mathbb K$. Les additions sont des « ou exclusifs », et les multiplications des « et ».

In [ ]:
def mul(A, B):
    n = len(A)
    C = n * [0]
    for i in range(n):
        for j in range(n):
            s = 0
            for k in range(n):
                s = s ^ (bit(A[i], k) & bit(B[k], j))
            C[i] += s << j
    return C

La fonction `random_inversible` renvoie un triplet $(A,B,c)$ où $A\in GL_n(\mathbb K)$, $B=A^{-1}$ et $c$ est le nombre d'essais effectués pour obtenir le résultat. 

In [ ]:
def random_inversible(n):
    c = 0
    while True:
        try:
            c += 1
            A = rand_mat(n)
            B = inverse(A)
            return A, B, c
        except Exception: continue

Testons. Prenons une matrice inversible $A$, la matrice $B$ qui est censée être son inverse, et calculons le produit $AB$. Celui-ci devrait être égal à $I_n$.

In [ ]:
A, B, c = random_inversible(8)
print(A)
print(B)
print(c)
print(mul(A, B) == eye(8))

## 4. Retour au jeu de l'électricien fou

### 4.1 Notre jeu favori

Revenons à notre jeu favori. Rappelons la matrice de passage de la base $\mathcal B_0$ à la base $\mathcal B$.

In [ ]:
P = transp(exemple)
print(P)

Au fait, $\mathcal B$ est-elle une base de $E$ ? C'est le cas si et seulement si $P$ est inversible.

In [ ]:
Q = inverse(P)
print(Q)

Oui, $\mathcal B$ est une base. Le vecteur $(1,\ldots,1)$ s'écrit donc de façon unique comme combinaison des éléments de $\mathcal B$. Voici la matrice de ce vecteur dans la base $\mathcal B_0$.

In [ ]:
Y = 8 * [1]
print(Y)

Le produit $X=P^{-1}Y$ est la solution du jeu.

In [ ]:
print(mul(Q, Y))

Nous obtenons ce que nous savions déjà depuis longtemps : pour terminer le jeu il suffit d'appuyer une fois sur chacun des boutons.

Remarquons que nous pouvions utiliser le pivot de Gauss directement sans passer par $P^{-1}$ :

In [ ]:
I, X = gauss(P, Y)
print(I)
print(X)

Ultime vérification, on doit avoir $PX=(1\ldots 1)^T$.

In [ ]:
mul(P, X)

### 4.2 Jeux aléatoires

Nous avons maintenant tout ce qu'il nous faut pour créer et résoudre des jeux aléatoires. Le jeu auquel nous avons joué était caractérisé par la liste `exemple`. Pour créer un jeu aléatoire, il suffit de tirer la règle au hasard. La seule condition imposée est que la matrice correspondante soit inversible, ce qui assure l'existence et l'unicité de la solution (modulo 2).

La fonction `random_jeu` renvoie un jeu aléatoire de taille $n$. Cette fonction est quasiment la même que `random_inversible`. La seule différence est qu'on impose à la matrice renvoyée d'avoir tous ses coefficients diagonaux égaux à 1 (pour que l'appui sur le bouton $k$ modifie l'état de la lampe $k$). Ceci est réalisé grâce à l'opérateur Python `|` qui effectue un ou *inclusif* sur les bits de ses arguments.

In [ ]:
def random_jeu(n):
    while True:
        try:
            A = rand_mat(n)
            for i in range(n):
                A[i] = A[i] | (2 ** i)
            B = inverse(A)
            return transp(A)
        except Exception: continue

In [ ]:
J = random_jeu(8)
print(J)

Ceci n'est pas très explicite. Écrivons une fonction qui affiche une description du jeu.

In [ ]:
def decrire(J):
    n = len(J)
    for k in range(n):
        s = str(k) + " -> "
        bs = [bit(J[k], i) for i in range(n)]
        for i in range(n):
            if bs[i] == 1:
                s += str(i) + ', '
        print(s[:-2])

Testons sur notre jeu favori.

In [ ]:
J = exemple
decrire(J)

Résoudre un jeu est immédiat. On « transpose » le jeu et on appelle `gauss`.

In [ ]:
def resoudre(J):
    n = len(J)
    P = transp(J)
    Y = n * [1]
    I, X = gauss(P, Y)
    return X

### 4.3 Quelques tests

Premier test, sur notre jeu favori.

In [ ]:
J = exemple
decrire(J)
X = resoudre(J)
print('\nSolution :', X)

Essayons maintenant le « jeu trivial » : l'appui sur le bouton $k$ change l'état de la lampe $k$, et seulement elle. Ce serait le cas d'une installation électrique effectuée par un électricien normal. Sans être un génie, on peut trouver la solution du jeu sans calculs :-).

In [ ]:
J = eye(8)
decrire(J)
X = resoudre(J)
print('\nSolution :', X)

Prenons un jeu aléatoire de taille 20.

In [ ]:
J = random_jeu(20)
decrire(J)
X = resoudre(J)
print('\nSolution :', X)

La création et la résolution d'un jeu de taille $n$ utilisent toutes les deux l'algorithme du pivot de Gauss dont la complexité est miraculeusement pour nous $O(n^2)$. On peut donc espérer pour voir créer et résoudre sans difficulté un jeu de taille 1000.

Créons le jeu. Ici, tout dépend de la chance puisqu'il faut créer une matrice inversible de taille 1000. Quelques secondes suffisent pourvu qu'on ne soit pas malchanceux.

In [ ]:
J = random_jeu(1000)

Résolvons le jeu. J'ai mis `print(X)` en commentaire parce que le résultat n'est pas vraiment passionnant.

In [ ]:
t1 = time.time()
X = resoudre(J)
t2 = time.time()
print(t2 - t1)
# print(X)

Sur mon vieil ordinateur de bureau, il faut 1.3 seconde. Sur mon portable, il faut environ 0.3 seconde. Remarquons la confirmation éclatante du fait que notre pivot de Gauss a ici la complexité inespérée $O(n^2)$. Si cette complexité était $O(n^3)$ cela aurait signifié que Python peut effectuer sur mon portable $1000^3$, c'est à dire 1 milliard, d'opérations en 0.3 seconde. J'adorerais ...

### 4.4 Représentation graphique

Terminons ce notebook en affichant graphiquement la solution d'un jeu. La fonction `plot_solution` prend en paramètre un jeu $J$. Si la solution du jeu comporte $c$ appuis sur des boutons, on affiche un grapique de $c+1$ lignes d'ordonnées 0, 1, ..., $c$. La ligne 0 est entièrement noire (lampes éteintes). Pour $i\in\bbr 1c$, la ligne $i$ représente l'état des lampes après appui sur le $i$ème bouton de la solution. En noir, les lampes éteintes. En blanc, les lampes allumées. La ligne $c$ est entièrement blanche (lampes allumées).

In [ ]:
def plot_solution(J, lines=True):
    n = len(J)
    Sol = resoudre(J)
    A = [n * [0]]
    x = 0
    c = 0
    for i in range(n):
        if Sol[i] == 1:
            c += 1
            x = x ^ J[i]
            A.append([bit(x, k) for k in range(n)])
    print('Nombre de coups :', c)
    plt.imshow(A, cmap='gray', interpolation='none', extent=(-0.5, n - 0.5, -0.5, c + 0.5), origin='lower')
    if lines:
        for i in range(c + 1):
            plt.plot([-0.5, n - 0.5], [i - 0.5, i - 0.5], 'k', lw=0.25)
        for i in range(n + 1):
            plt.plot([i - 0.5, i - 0.5], [-0.5, c + 0.5], 'k', lw=0.25)

Voici la solution de notre jeu favori

In [ ]:
plot_solution(exemple, True)

La solution du jeu trivial va de soi. On allume les lampes les unes après les autres.

In [ ]:
plot_solution(eye(8), True)

Un jeu aléatoire de taille 50 ?

In [ ]:
plot_solution(random_jeu(50), True)
plt.savefig('fig01.png', bbox_inches='tight')

Pour fêter la fondation de Rome, terminons par un jeu aléatoire de taille 753.

In [ ]:
plot_solution(random_jeu(753), False)
plt.savefig('fig01.png', bbox_inches='tight')

Quand on regarde l'aspect *apparemment* chaotique de ce graphique, on se dit qu'arriver à allumer les lampes manuellement en appuyant physiquement sur les boutons aurait été assez délicat ...